In [86]:
import os
import sys
from stat import *
from mylist import *
from random import randrange
from mystat import *

# cmp function for list lookups
# cmp node objects 
def node_obj_cmp(node, obj):
    if node.nobj == obj:
        return True
    else:
        return False

# compare object names

def node_objname_cmp(node, name):
    if node.nobjname == name:
        return True
    else:
        return False

def node_objid_cmp(node, id):
    if node.nobjid == id:
        return True
    else:
        return False

# file objects 
# mandatory to have these members.
# name - file name (not the full path)
# objid - file object is thisis the inode no. in the stat
# stat - stat object of the file returned by os.stat api.
# dir 0 (default) implies it is not directory but a regular file.
# dir 1 implies it is a directory.
# 

class myfile():

    # look above for argument descriptions.
    # raise exception if dir is 1 and not a dir
    # raise exception fi dir is 0 and not a regular file.
    # DO NOT CHANGE THIS. 
    # you can add additional members if required.

    def __init__(self, objid, name=None, stat=None, dir=0):

        # leave the following in there.
        if name and '/' in name:
            raise Exception("Bad name in file")
        if dir and stat and not S_ISDIR(stat.st_mode):
            s=f'{name} is not a directory'
            raise Exception(s)
        if not dir and stat and not S_ISREG(stat.st_mode):
            s=f'{name} is not a file'
            raise Exception(s)

        self.name=name
        self.objid = objid
        self.stat=stat
        self.dir=dir
        self.path=None
        self.size=None

    
    # return the file path from root of the tree to which it belongs.
    # eg., I will create a file object with
    # fobj=myfile(241573) ie. only with objectid.
    # print(fobj.path(tree))
    # where this file is part of the tree.  Note: not this instance
    # of the object but the same objectid.
    # it should print the file path.
    # the objectid is found by "ls -i1" in any of the subdirectory
    # of the kernel-0 folder sent to you.  you can do that even on windows
    # with powershell i believe.
    # this function should print the full path of that objectid starting
    # from the kernel-0 folder.
    # eg., if the file kernel-0/mm/f1.c and its objectid is 241573
    # then fobj.file_path(tree) should print kernel-0/mm/f1.c
    # Note: this has to be recalculated from the tree when this function
    # is called. Tree was the object obtained from convert_to tree function
    # at the end of this file.


    def file_path(self, tree):
        pass
        #YOUR CODE
        raise NotImplementedError

    # return the file size
    # required for the binary tree organization of these file objects.
    # for assignment 6.
    #

    def file_size(self):
        return self.size

    # this is just a helper. feel free to modify the way you want it to help
    # you.

    def __str__(self):
        return f'File Name: {self.name}'

# directory objects inherit from file, uses 
# all of what file has plus some more interfaces.


class mydir(myfile):

    # DO NOT CHANGE THIS.
    # you can add any members below this.

    def __init__(self, objid, name=None, stat=None, ):
        super().__init__(objid, name, stat, 1)
        self.path=None
        
    def __str__(self):
        return f'Folder Name: {self.name}'
    
    
    # find the total no. of files underneath this directory including 
    # the directories (as they are also files) as well. 
    # eg., if you have a folder : kernel-0/mm/f1.c and kernel-0/mm/f2.c
    # dir_total_files of the directory kernel-0 will print : 3. two regular
    # files and one directory file "mm".
    # use case will be :
    # dir=mydir(245173)
    # dir.dir_total_files(tree)
    # where this directory is part of the tree.  Note: not this instance
    # of the object but the same objectid.
    # Note this has to be "calculated" every time the function is called
    # from the passed tree. 

    def dir_total_files(self, tree):
        #YOUR CODE
        raise NotImplementedError
        pass

    # the below function is similar as above but should print the only the total
    # no. of directories underneath this directory.
    # Note this has to be "calculated" every time the function is called
    # from the passed tree. 

    def dir_total_dirs(self, tree):
        pass
        #YOUR CODE
        raise NotImplementedError


class mynode():
    # pobj - parent object
    # obj - this object
    # objname - name of this object
    # objid - unique id of this object. for file and dir it is inode numbes.
    # Do not change this.

    def __init__(self, pobj, obj, objname, objid):
        self.child_list=mylist("list")
        self.nobj=obj
        self.nobjname = objname
        self.nobjid=objid
        self.npobj = pobj

class mytree():

# init functionf or root object and name and its object id.
# (object id for these objects are all inode numbers).
# Do not change this.

    def __init__(self, obj, root_name, id):
        self.root=mynode(None, obj, root_name, id)
        self.total_nodes=1
        self.root.path='kernel-0'

# the following two functions are helper functions for 
# constructing the tree, insertions etc..



# Lookup objname from a parent node, if found return
# node object. 
# If it does not  exist, create a node for that objname,
# objid combinations, ensure to add it to the appropriate child
# list.

    def lookup_create(self, pobj:mynode, objname, objid, obj):
        if self.lookup(pobj,objname)==None:
            obj_node=mynode(pobj,obj,objname,objid)
            self.child_list.add(obj_node)
            self.total_nodes+=1

# Lookup objname from a parent node, if found return
# node object. If not, return None.

    def lookup(self, pobj:mynode, objname):
        child_list=pobj.child_list
        for child in child_list:
            if child.nobjname==objname:
                return child
           
    def print_tree(self):
        root=self.root
        print(f'{root.nobj.name} Child: ', end="")
        for i in root.child_list:
            print(f'{i.obj.name}, ', end="")
        print('\n')
        for i in root.child_list:
            self.dump1(i) 


# Method on the tree object to traverse and it will call the function
# func with the passed arguments (variable argument args), for 
# every line of the object it will generate as output corresponding 
# to the input file in function convert_input_to_tree().
#
# for the eg. mentioned in the comments of that function
# the function func() will get called for each of the
# lines given there. And that string will be passed as first argument to the
# function.

# func_traverse(tree, test_func, argobj) returned by convert_input_to_tree() will call 
# test_func(fobj, "kernel-0", argobj) where fobj is the mydir obj for kernel-0.
# test_func(fobj, "kernel-0/arch", argobj) where fobj is the mydir obj for kernel-0/arch.
# test_func(fobj, "kernel-0/arch/boot", argobj) where fobj is the mydir obj for kernel-0/arch/boot.
# test_func(fobj, "kernel-0/arch/boot/bootloader.lds", argobj) where fobj is the  myfile obj 
# for kernel-0/arch/boot/bootloader.lds.

# you can test this function by putting the string in some file or std output
# and then compare the entire output with the original input file (sort both to
# avoid any ordering issues).

    def func_traverse(self, func, *args):
        #YOUR CODE
        raise NotImplementedError
        pass

# exactly same as above function except that the traversal starts
# from an intermediary mynode() object ie., an interior node.

    def func_node_traverse(self, node, func, *args):
        #YOUR CODE
        raise NotImplementedError
        pass

# some debug stuff may be useful.

    def dump1(self, root):
        print(root.obj)
        print(f'{root.obj} Child: ', end="")
        for i in root.child_list:
            print(f'{i.obj}, ', end="")
        print('\n')
        for i in root.child_list:
            self.dump1(i)

# some debug stuff may be useful.

    def dump(self):
        print(f'Total Nodes: {self.total_nodes}')
        self.dump1(self.root)


# Function takes an input file name 
# and converts that into an object instance of 
# the tree class as defined above.
# you can only use the operations given above to construct the tree.
# no other functions should be added.
# input file will be of the form:
#kernel-0
#kernel-0/arch
#kernel-0/arch/alpha
#kernel-0/arch/alpha/boot
#kernel-0/arch/alpha/boot/bootloader.lds
# the above should be converted to tree with root object being the
# directory object - kernel-0, and there are arch, alpha and boot as
# directory objects below and bootloader.lds as a file object below.
# construct the appropriate hierarchy. The mynode.obj should be 
# either a mydir or myfile object as defined above.

# returns "tree" object.

# hint use readlines, strip, and split if required  and os.stat

def convert_input_to_tree(filename):
    file=open(filename,'r')
    lines=file.readlines()
    
    # Initialise the tree and initialise the root object
    root_location='kernel-0' # Initilize the root location
    stats=mystat(root_location) # Get the stats from mystat()
    inode=stats.st_ino  # Find the inode number
    root_object=mydir(inode,root_location,stats) # Create a root object
    filetree=mytree(root_object,root_location,inode) # Create a tree with root node
    
    #Initialise the parent node
    parent_node=filetree.root # Initialise the parent_node to the root node
    
    for line in lines:
        line=line.strip()
     
        #Split the path into individual components
        path_list=line.split('/')
        path=root_location+'/'
        for iterator in range(1,len(path_list)):
            
            path+=path_list[iterator]+'/' # Creating the path of each object
            stats=mystat(path[:-1]) # Get the stats of the file
            inode=stats.st_ino # Get the inode number
            filename=path.split('/') 
            filename=filename[-2] # Get the filename
            mode=stats.st_mode  # Get the mode of file/directory
            directory=S_ISDIR(mode) # Check of the object is file or directory
            
            
            dir_object=None
            dir_node=None
            file_node=None
            file_object=None

            if directory: # means the object is a directory
                
                # Create Directory object
                dir_object=mydir(inode,filename,stats)
                dir_node=mynode(parent_node,dir_object,filename,inode)
                print(parent_node,filename)
                if filetree.lookup(parent_node,filename)==None:
                    print('Already present')
                else:
                    print('Not present')
                parent_node=dir_node


    return filetree



In [87]:
filename='kernel-0.files'
tree=convert_input_to_tree(filename)

<__main__.mynode object at 0x7f7e97d6a550> arch
Already present
<__main__.mynode object at 0x7f7e96db2430> arch
Already present
<__main__.mynode object at 0x7f7e9798b1c0> alpha
Already present
<__main__.mynode object at 0x7f7e9798bee0> arch
Already present
<__main__.mynode object at 0x7f7e96e0f250> alpha
Already present
<__main__.mynode object at 0x7f7e976f1250> boot
Already present
<__main__.mynode object at 0x7f7e976f1df0> arch
Already present
<__main__.mynode object at 0x7f7e97725b50> alpha
Already present
<__main__.mynode object at 0x7f7e978284c0> boot
Already present
<__main__.mynode object at 0x7f7e97828af0> arch
Already present
<__main__.mynode object at 0x7f7e972256d0> alpha
Already present
<__main__.mynode object at 0x7f7e97225790> boot
Already present
<__main__.mynode object at 0x7f7e973ae700> arch
Already present
<__main__.mynode object at 0x7f7e97752310> alpha
Already present
<__main__.mynode object at 0x7f7e977528e0> boot
Already present
<__main__.mynode object at 0x7f7e97

In [41]:
tree.print_tree()

kernel-0 Child: 



In [43]:
mystat('kernel-0/arch/alpha/kernel/setup.c')

os.stat_result(st_mode=33188, st_ino=2492620, st_dev=76, st_nlink=1, st_uid=1000, st_gid=1000, st_size=39244, st_atime=1636943264, st_mtime=1636237426, st_ctime=1636943297)

In [45]:
mystat('kernel-0/arch/alpha/kernel')

os.stat_result(st_mode=16877, st_ino=2492612, st_dev=76, st_nlink=1, st_uid=1000, st_gid=1000, st_size=1572, st_atime=1636943202, st_mtime=1636237426, st_ctime=1636943203)

In [46]:
S_ISDIR(16877)

True